# Playing around with Machine to Machine API access

## Let's do some EagleEye setup

In [ ]:
import logging
logger = logging.getLogger()
logger.setLevel('INFO')

In [ ]:
from EagleEyev3 import *
from settings import config

In [ ]:
een = EagleEyev3(config)

In [ ]:
een.__version__

## Let's do some DB setup

In [ ]:
import sqlite3

In [ ]:
con = sqlite3.connect('instance/project.db')

In [ ]:
cur = con.cursor()

## Login as a user with their refresh_token and query their cameras

In [ ]:
if een.refresh_token == None or een.refresh_token == '':
    # if you get out of sync you manually copy a refresh_token here to get the loop started
    een.refresh_token = ''

In [ ]:
een.login_tokens(code=None, cascade=True, refresh_token=een.refresh_token)

In [ ]:
een.refresh_token

In [ ]:
een.get_base_url()

In [ ]:
_ = een.get_list_of_cameras()

In [ ]:
een.cameras

In [ ]:
r2d2 = een.cameras[3]

In [ ]:
r2d2.get_list_of_videos(start_timestamp=een.time_before(hours=24*14), end_timestamp=een.time_now())

In [ ]:
len(r2d2.videos)

## Poke around in the DB

In [ ]:
for row in cur.execute('SELECT * FROM download WHERE camera_id = 53 limit 10'):
    pass

In [ ]:
sql = """
SELECT
	user.email,
	camera.name,
	download.url,
	count(download.url)
FROM
	camera
	JOIN download ON download.camera_id = camera.id
	JOIN USER ON camera.user_id = user.id
WHERE
	download.status = 'new'
GROUP BY
	camera.name
ORDER BY
	count(download.url)
	DESC;
"""

## Try downloading a video ##

In [ ]:
r2d2.videos[9]

In [ ]:
import requests

In [ ]:
#req = requests.get(url=benny.videos[9]['mp4Url'], headers={"Authorization": f"Bearer {een.access_token}"})

In [ ]:
#req.headers

In [ ]:
#benny.save_video_to_file(url=benny.videos[9]['mp4Url'], filename='benny9.mp4')

In [ ]:
sql = '''SELECT
	download.id,
	download.url,
    camera.device_id,
	download.start_timestamp,
    download.end_timestamp
FROM
	camera
	JOIN download ON download.camera_id = camera.id
	JOIN USER ON camera.user_id = user.id
WHERE
	download.status == 'new' 
	and camera.id == 4;'''

In [ ]:
from tqdm import tqdm


In [ ]:
for row in tqdm(cur.execute(sql)):
    fname = f"videos/{row[2]}/{row[2]}_{row[3]}-{row[4]}.mp4"
    #print(fname)
    r2d2.save_video_to_file(url=row[1], filename=fname)